# CS117 Final Project

**name: Daniel Du**

**SID: 45054949**

In [14]:
import numpy as np
import matplotlib.pyplot as plt
from camutils import *
import meshutils
import pickle
import visutils
import cv2
import matplotlib.patches as patches
from mpl_toolkits.mplot3d import Axes3D

%matplotlib inline

In [15]:
# load in the intrinsic camera parameters from 'calibration.pickle'
file = open("calibration.pickle","rb")
param = pickle.load(file)

# create Camera objects representing the left and right cameras
# use the known intrinsic parameters you loaded in.
camL = Camera(f = (param['fx']+param['fy'])/2,c = np.array([[param['cx'],param['cy']]]).T,t=np.array([[0,0,0]]).T, R=makerotation(0,0,0))
camR = Camera(f = (param['fx']+param['fy'])/2,c = np.array([[param['cx'],param['cy']]]).T,t=np.array([[0,0,0]]).T, R=makerotation(0,0,0))


# load in the left and right images and find the coordinates of
# the chessboard corners using OpenCV
imgL = plt.imread('images/calib_jpg_u/frame_C0_01.jpg')
ret, cornersL = cv2.findChessboardCorners(imgL, (8,6), None)
pts2L = cornersL.squeeze().T

imgR = plt.imread('images/calib_jpg_u/frame_C1_01.jpg')
ret, cornersR = cv2.findChessboardCorners(imgR, (8,6), None)
pts2R = cornersR.squeeze().T

# generate the known 3D point coordinates of points on the checkerboard in cm
pts3 = np.zeros((3,6*8))
yy,xx = np.meshgrid(np.arange(8),np.arange(6))
pts3[0,:] = 2.8*xx.reshape(1,-1)
pts3[1,:] = 2.8*yy.reshape(1,-1)


# Now use your calibratePose function to get the extrinsic parameters
# for the two images. You may need to experiment with the initialization
# in order to get a good result

camL = calibratePose(pts3,pts2L,camL,np.array([0,160,0,20,0,40]))
camR = calibratePose(pts3,pts2R,camR,np.array([-20,180,0,20,-10,25]))

print(camL)
print(camR)

Camera : 
 f=1404.6126896357434 
 c=[[962.16384328 590.92528144]] 
 R=[[ 0.03843677  0.98947349  0.1395164 ]
 [ 0.97735757 -0.00815333 -0.21143723]
 [-0.20807401  0.14448437 -0.96738279]] 
 t = [[ 6.86592254 19.52347749 47.34466544]]
Camera : 
 f=1404.6126896357434 
 c=[[962.16384328 590.92528144]] 
 R=[[-0.00259821  0.99096857  0.13406916]
 [ 0.99277869 -0.01352314  0.11919562]
 [ 0.11993215  0.1334107  -0.98377735]] 
 t = [[ 7.50033701  7.20907039 47.76536775]]


In [16]:
def decode(imprefix,start,threshold):
    """
    Given a sequence of 20 images of a scene showing projected 10 bit gray code, 
    decode the binary sequence into a decimal value in (0,1023) for each pixel.
    Mark those pixels whose code is likely to be incorrect based on the user 
    provided threshold.  Images are assumed to be named "imageprefixN.png" where
    N is a 2 digit index (e.g., "img00.png,img01.png,img02.png...")
 
    Parameters
    ----------
    imprefix : str
       Image name prefix
      
    start : int
       Starting index
       
    threshold : float
       Threshold to determine if a bit is decodeable
       
    Returns
    -------
    code : 2D numpy.array (dtype=float)
        Array the same size as input images with entries in (0..1023)
        
    mask : 2D numpy.array (dtype=logical)
        Array indicating which pixels were correctly decoded based on the threshold
    
    """
    
    # we will assume a 10 bit code
    nbits = 10
    
    # get all names
    names = []
    
    
    for i in range(start,start+20):
        if i < 10:
            num = "0"+str(i)
        else:
            num = str(i)
        names.append(imprefix+num+".png")
        
    shape = plt.imread(names[0]).shape
    
    # get differences
    pics = []
    
    for i in range(nbits):
        img1 = plt.imread(names[i*2])
        img2 = plt.imread(names[(i*2) + 1])
        
        # convert to grayscale
        if len(shape) > 2:
            r, g, b = img1[:,:,0], img1[:,:,1], img1[:,:,2]
            img1 = 0.2989 * r + 0.5870 * g + 0.1140 * b
            r, g, b = img2[:,:,0], img2[:,:,1], img2[:,:,2]
            img2 = 0.2989 * r + 0.5870 * g + 0.1140 * b
        
        pics.append(img1-img2)
        
    shape = pics[0].shape
    
    # create mask and code
    code = np.zeros(shape, dtype = int)
    mask = np.ones(shape, dtype = bool)
    
    #get value of pixels
    for i in range(shape[0]):
        for j in range(shape[1]):
            bits = []
            decimal = 0
            for a in range(nbits):
                if abs(pics[a][i,j]) < threshold:
                    mask[i,j] = False
                    code[i,j] = 0
                    break
                elif pics[a][i,j] < 0:
                    bits.append(0)
                else:
                    bits.append(1)
            if len(bits) == nbits:
                first = 0
                for a in range(nbits):
                    first = (first+bits[a]) % 2
                    decimal += first * (2**(nbits-a-1))
                code[i,j] = decimal
             
    
        
    return code,mask

In [17]:
def reconstruct(imprefix,threshold,camL,camR):
    """
    Performing matching and triangulation of points on the surface using structured
    illumination. This function decodes the binary graycode patterns, matches 
    pixels with corresponding codes, and triangulates the result.
    
    The returned arrays include 2D and 3D coordinates of only those pixels which
    were triangulated where pts3[:,i] is the 3D coordinte produced by triangulating
    pts2L[:,i] and pts2R[:,i]

    Parameters
    ----------
    imprefixL, imprefixR : str
        Image prefixes for the coded images from the left and right camera
        
    threshold : float
        Threshold to determine if a bit is decodeable
   
    camL,camR : Camera
        Calibration info for the left and right cameras
        
    Returns
    -------
    pts2L,pts2R : 2D numpy.array (dtype=float)
        The 2D pixel coordinates of the matched pixels in the left and right
        image stored in arrays of shape 2xN
        
    pts3 : 2D numpy.array (dtype=float)
        Triangulated 3D coordinates stored in an array of shape 3xN
        
    """
    #fore/back ground masking
    thresh = 0.01
    
    back0 = plt.imread(imprefix+"color_C0_00.png")
    fore0 = plt.imread(imprefix+"color_C0_01.png")
    back1 = plt.imread(imprefix+"color_C1_00.png")
    fore1 = plt.imread(imprefix+"color_C1_01.png")
    
    mask = abs(fore0-back0)
    mask = (mask[:,:,0] + mask[:,:,1] + mask[:,:,2])/3
    
    mask0 = np.ones((mask.shape[0],mask.shape[1]), dtype = bool)
    for i in range(mask.shape[0]):
        for j in range(mask.shape[1]):
            if mask[i,j] > thresh:
                mask0[i,j] = False
    mask = abs(fore1-back1)
    mask = (mask[:,:,0] + mask[:,:,1] + mask[:,:,2])/3
    mask1 = np.ones((mask.shape[0],mask.shape[1]), dtype = bool)
    for i in range(mask.shape[0]):
        for j in range(mask.shape[1]):
            if mask[i,j] > thresh:
                mask1[i,j] = False
    
    # Decode the H and V coordinates for the two views
    H0,H0mask = decode(imprefix+"frame_C0_",0,threshold)
    V0,V0mask = decode(imprefix+"frame_C0_",20,threshold)
    H1,H1mask = decode(imprefix+"frame_C1_",0,threshold)
    V1,V1mask = decode(imprefix+"frame_C1_",20,threshold)
    
    # Construct the combined 20 bit code C = H + 1024*V and mask for each view
    C0 = H0 + (1024*V0)
    C0mask = np.logical_or(~H0mask,~V0mask)
    C1 = H1 + (1024*V1)
    C1mask = np.logical_or(~H1mask,~V1mask)

    C0mask = np.logical_or(C0mask,mask0)
    C1mask = np.logical_or(C1mask,mask1)
    
    # Find the indices of pixels in the left and right code image that 
    # have matching codes. If there are multiple matches, just
    # choose one arbitrarily.

    CL = np.ma.masked_array(C0,C0mask)
    CR = np.ma.masked_array(C1,C1mask)
    
    matches,matchL,matchR = np.intersect1d(CL,CR,return_indices=True)
    
    # Let CL and CR be the flattened arrays of codes for the left and right view
    # Suppose you have computed arrays of indices matchL and matchR so that 
    # CL[matchL[i]] == CR[matchR[i]] for all i.  The code below gives one approach
    # to generating the corresponding pixel coordinates for the matched pixels.

    
    w = CL.shape[1]
    h = CL.shape[0]
    
    xx,yy = np.meshgrid(range(w),range(h))
    xx = np.reshape(xx,(-1,1))
    yy = np.reshape(yy,(-1,1))
    pts2R = np.concatenate((xx[matchR].T,yy[matchR].T),axis=0)
    pts2L = np.concatenate((xx[matchL].T,yy[matchL].T),axis=0)
    
    colors = np.empty((3,pts2R.shape[1]),dtype = float)
    for i in range(pts2R.shape[1]):
        colors[0,i] = (fore0[pts2L[1,i],pts2L[0,i]][0] + fore1[pts2R[1,i],pts2R[0,i]][0])/2
        colors[1,i] = (fore0[pts2L[1,i],pts2L[0,i]][1] + fore1[pts2R[1,i],pts2R[0,i]][1])/2
        colors[2,i] = (fore0[pts2L[1,i],pts2L[0,i]][2] + fore1[pts2R[1,i],pts2R[0,i]][2])/2
    
    # Now triangulate the points
    pts3 = triangulate(pts2L,camL,pts2R,camR)

    return pts2L,pts2R,pts3,colors

In [18]:
#
# Reconstruct and visualize the results
#
index = '3'

imprefix = 'images/croc/grab_'+index+'_u/'
threshold = 0.02

print(camL)
print(camR)

pts2L,pts2R,pts3,colors = reconstruct(imprefix,threshold,camL,camR)

Camera : 
 f=1404.6126896357434 
 c=[[962.16384328 590.92528144]] 
 R=[[ 0.03843677  0.98947349  0.1395164 ]
 [ 0.97735757 -0.00815333 -0.21143723]
 [-0.20807401  0.14448437 -0.96738279]] 
 t = [[ 6.86592254 19.52347749 47.34466544]]
Camera : 
 f=1404.6126896357434 
 c=[[962.16384328 590.92528144]] 
 R=[[-0.00259821  0.99096857  0.13406916]
 [ 0.99277869 -0.01352314  0.11919562]
 [ 0.11993215  0.1334107  -0.98377735]] 
 t = [[ 7.50033701  7.20907039 47.76536775]]


In [19]:
import scipy

# Mesh cleanup parameters

# Specify limits along the x,y and z axis of a box containing the object
# we will prune out triangulated points outside these limits

#boxlimits = np.array([-200,400,-200,300,-200,200])

# Specify a longest allowed edge that can appear in the mesh. Remove triangles
# from the final mesh that have edges longer than this value
trithresh = 1

#
# triangulate the 2D points to get the surface mesh
#

tri = scipy.spatial.Delaunay(pts2L.T).simplices

#
# triangle pruning
#

to_del = np.array([],dtype = int)
trans = pts3.T
for i in range(tri.shape[0]):
    tripts = trans[tri[i]]
    if (max(np.linalg.norm(tripts[0] - tripts[1]),np.linalg.norm(tripts[1] - tripts[2]),np.linalg.norm(tripts[2] - tripts[0])) > trithresh):
        to_del = np.append(to_del,i)
        
tri = np.delete(tri,to_del,0)


#
# remove any points which are not refenced in any triangle
#

filled = np.arange(pts3.shape[1])
tokeep = np.intersect1d(filled,tri)

map_arr = np.zeros(pts3.shape[1])
map_arr[tokeep] = np.arange(0,tokeep.shape[0])

tri = map_arr[tri]

to_del = np.setxor1d(filled,tokeep)            
pts3 = np.delete(pts3,to_del,1)
colors = np.delete(colors,to_del,1)




In [20]:
def avgpts(pts3,points,index):
    output = 0;
    for point in points:
        output += pts3[index,point]
    return output/len(points)

for times in range(5):
    #smoothing
    sets = [set() for x in range(pts3.shape[1])]
    pts3cpy = np.copy(pts3)

    for i in range(tri.shape[0]):
        sets[int(tri[i,0])].add(int(tri[i,1]))
        sets[int(tri[i,0])].add(int(tri[i,2]))
        sets[int(tri[i,1])].add(int(tri[i,0]))
        sets[int(tri[i,1])].add(int(tri[i,2]))
        sets[int(tri[i,2])].add(int(tri[i,0]))
        sets[int(tri[i,2])].add(int(tri[i,1]))

    for i in range(pts3.shape[1]):
        pts3[0,i] = avgpts(pts3cpy,sets[i],0)
        pts3[1,i] = avgpts(pts3cpy,sets[i],1)
        pts3[2,i] = avgpts(pts3cpy,sets[i],2)

In [21]:
# vis code goes here
import trimesh

meshutils.writeply(pts3,colors,tri,"croc"+index+".ply")

mesh = trimesh.Trimesh(vertices=pts3.T,faces=tri[:,[0,2,1]])
mesh.show()